In [1]:
from IPython.display import display, HTML 
display(HTML("<style>.container { width:80% !important; }</style>"))

## Imports

In [2]:
import numpy as np
import pandas as pd

from datetime import timedelta, datetime

import sqlite3

import re

import plotly.graph_objects as go
from plotly.subplots import make_subplots
from dash import Dash, dcc, html, Input, Output, State

## Read in the data

In [3]:
database = "./Noise Data/TVAR20233_noise_data.sqlite"
db_connection = sqlite3.connect(database)
query = ("SELECT * FROM noise")

df = pd.read_sql_query(query, db_connection)
db_connection.close()

df["time"] = pd.to_datetime(df["time"], unit='s')
df

time  m_altimeter_status  m_digifin_status  \
0     2023-11-09 07:07:55.036000000                 1.0               0.0   
1     2023-11-09 07:07:59.043000064                 1.0               0.0   
2     2023-11-09 07:08:03.045000192                 1.0               0.0   
3     2023-11-09 07:08:07.046999808                 2.0               0.0   
4     2023-11-09 07:08:11.048999936                 2.0               0.0   
...                             ...                 ...               ...   
32347 2023-11-10 23:56:25.364000000                 2.0               2.0   
32348 2023-11-10 23:56:29.365999872                 2.0               2.0   
32349 2023-11-10 23:56:33.368999936                 2.0               0.0   
32350 2023-11-10 23:56:37.372000000                 2.0               2.0   
32351 2023-11-10 23:56:41.374000128                 2.0             258.0   

          m_fin  m_is_ballast_pump_moving  m_is_battpos_moving  m_fin_diff  \
0      0.000000                       1.0                  1.0         NaN   
1      0.000000                       1.0                  0.0    0.000000   
2      0.000000                       1.0                  0.0    0.000000   
3      0.000000                       0.0                  0.0    0.000000   
4      0.000000                       0.0                  0.0    0.000000   
...         ...                       ...                  ...         ...   
32347  0.112899                       0.0                  0.0    0.115794   
32348 -0.002895                       0.0                  0.0   -0.115794   
32349 -0.002895                       0.0                  0.0    0.000000   
32350 -0.002895                       0.0                  0.0    0.000000   
32351 -0.002895                       0.0                  0.0    0.000000   

       is_fin_moving      m_lat      m_lon  ...  ship_0_distance  \
0                NaN  60.203570  24.960154  ...              NaN   
1                0.0  59.844882  23.249485  ...              NaN   
2                0.0  59.844882  23.249483  ...              NaN   
3                0.0  59.844882  23.249482  ...              NaN   
4                0.0  59.844880  23.249475  ...              NaN   
...              ...        ...        ...  ...              ...   
32347            1.0        NaN        NaN  ...              NaN   
32348            1.0        NaN        NaN  ...              NaN   
32349            0.0        NaN        NaN  ...              NaN   
32350            0.0        NaN        NaN  ...              NaN   
32351            0.0        NaN        NaN  ...              NaN   

       ship_1_distance  jussarö_wind_speed  jussarö_wind_direction  \
0                  NaN            3.712554              246.791727   
1                  NaN            3.718565              246.798405   
2                  NaN            3.724568              246.805075   
3                  NaN            3.730570              246.811745   
4                  NaN            3.736573              246.818415   
...                ...                 ...                     ...   
32347              NaN            6.778863              185.642273   
32348              NaN            6.775528              185.648943   
32349              NaN            6.772193              185.655615   
32350              NaN            6.768857              185.662287   
32351              NaN            6.765522              185.668957   

       jussarö_gust_speed  jussarö_potential_wind  russarö_wind_speed  \
0                5.637518                3.333381            5.445791   
1                5.639522                3.338724            5.441116   
2                5.641523                3.344060            5.436447   
3                5.643523                3.349396            5.431779   
4                5.645524                3.354732            5.427110   
...                   ...                     ...                 ...   


In [4]:
noise_df = df.copy()

## Set data limits

In [5]:
start_time = datetime.strptime("2023-11-09 09:00:00","%Y-%m-%d %H:%M:%S")
end_time   = datetime.strptime("2023-11-09 09:15:00","%Y-%m-%d %H:%M:%S")

In [6]:
distance_cols = re.compile(".*distance")
distance_cols = list(filter(distance_cols.match, noise_df.columns))

categorical_columns = ["m_altimeter_status", 
                       "m_digifin_status", "is_fin_moving", 
                       "m_is_ballast_pump_moving", "m_is_battpos_moving"]

numerical_columns = ["m_depth"] + distance_cols

In [7]:
# Subset data by time
df = noise_df[(noise_df["time"] > start_time) & 
              (noise_df["time"] < end_time)]

# Create list of appropriate timesteps
time_interval_steps = [start_time + timedelta(seconds=x) for x in range(0, (end_time-start_time).seconds)]

# Take relevant columns, add our timesteps
df = df[["time"] + categorical_columns + numerical_columns].merge(pd.DataFrame({"time":time_interval_steps}), how='outer', on="time")

# Forward fill categorical values to timesteps
df = df.sort_values(by=["time"])
df[categorical_columns] = df[categorical_columns].ffill()

# Interpolate numerical values to fill timesteps
df.set_index("time", inplace=True)
for col in numerical_columns:
    df[col].interpolate(method='time', inplace=True, limit_direction="forward", limit_area="inside")
df.reset_index(inplace=True)

# Remove original values not in timesteps
df = df.loc[df["time"].isin(time_interval_steps)].reset_index(drop=True)
df

time  m_altimeter_status  m_digifin_status  is_fin_moving  \
0   2023-11-09 09:00:00                 NaN               NaN            NaN   
1   2023-11-09 09:00:01                 NaN               NaN            NaN   
2   2023-11-09 09:00:02                 NaN               NaN            NaN   
3   2023-11-09 09:00:03                 NaN               NaN            NaN   
4   2023-11-09 09:00:04                 NaN               NaN            NaN   
..                  ...                 ...               ...            ...   
895 2023-11-09 09:14:55                 0.0               0.0            0.0   
896 2023-11-09 09:14:56                 0.0               0.0            0.0   
897 2023-11-09 09:14:57                 0.0               0.0            0.0   
898 2023-11-09 09:14:58                 0.0               0.0            0.0   
899 2023-11-09 09:14:59                 0.0               0.0            0.0   

     m_is_ballast_pump_moving  m_is_battpos_moving    m_depth  \
0                         NaN                  NaN        NaN   
1                         NaN                  NaN        NaN   
2                         NaN                  NaN        NaN   
3                         NaN                  NaN        NaN   
4                         NaN                  NaN        NaN   
..                        ...                  ...        ...   
895                       0.0                  0.0  31.353858   
896                       0.0                  0.0  31.535213   
897                       0.0                  0.0  31.716568   
898                       0.0                  0.0        NaN   
899                       0.0                  0.0        NaN   

     glider_distance  ship_0_distance  ship_1_distance  
0                NaN              NaN              NaN  
1                NaN              NaN              NaN  
2                NaN              NaN              NaN  
3                NaN              NaN              NaN  
4                NaN              NaN              NaN  
..               ...              ...              ...  
895         0.155171              NaN         0.159609  
896         0.155019              NaN         0.159739  
897         0.154867              NaN         0.159869  
898              NaN              NaN              NaN  
899              NaN              NaN              NaN  

[900 rows x 10 columns]

## Visualisation

### Categoricals only

In [8]:
# Base structure of plot
fig = make_subplots(rows=len(categorical_columns), cols=1,
                    shared_xaxes=True,
                    vertical_spacing=0.02)

# Add subplots
for i, col in enumerate(categorical_columns):
    fig.add_trace(go.Scatter(x=df["time"], y=df[col], line_shape='hv', name=col), row=i+1, col=1)
    fig.update_yaxes(type='category', categoryorder='array', categoryarray=np.sort(df[col].unique()), row=i+1, col=1)

fig.update_layout(height=len(categorical_columns)*100, width=1300)

# Create animation frames for vertical line
frames = [go.Frame(layout=dict(shapes=[dict(type="line", xref=f"x{n+1}", yref=f"y{n+1}",
                                            x0=df["time"][i], y0=0, 
                                            x1=df["time"][i], y1=len(df[col].unique())-2, 
                                            line_width=3) for n,col in enumerate(categorical_columns)]), 
                   name=str(df["time"][i])) for i in df.index]
fig.update(frames=frames)

# Helper function for slider and buttons
def frame_args(duration):
    return {
            "frame": {"duration": duration},
            "mode": "immediate",
            "fromcurrent": True,
            "transition": {"duration": duration, "easing": "linear"},
        }

fr_duration=1000  # Frame duration in milliseconds

sliders = [
            {
                "pad": {"b": 10, "t": 50},
                "len": 0.9,
                "x": 0.1,
                "y": 0,
                "transition": {"duration": fr_duration},
                "steps": [
                    {
                        "args": [[f.name], frame_args(fr_duration)],
                        "label": f.name,
                        "method": "animate"
                    }
                    for k, f in enumerate(fig.frames)
                ],
            }
        ]


fig.update_layout(sliders=sliders,
                  updatemenus = [
                        {
                        "buttons": [
                            {
                             "args": [None, frame_args(fr_duration)],
                             "label": "&#9654;", # play symbol
                             "method": "animate",
                            },
                            {
                             "args": [[None], frame_args(fr_duration)],
                             "label": "&#9724;", # pause symbol
                             "method": "animate",
                            }],
                        "direction": "left",
                        "pad": {"r": 10, "t": 70},
                        "type": "buttons",
                        "x": 0.1,
                        "y": 0,
                        }])

fig.show()

c:\Users\vaisanee\AppData\Local\anaconda3\envs\gliderwork\Lib\site-packages\_plotly_utils\basevalidators.py:105: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



### In-depth view

In [9]:
# Base structure of plot
specs = len(categorical_columns)*[[{}, None, None]]
specs[0] = [{}, {"rowspan": 5}, {"rowspan": 5}]
cols = 3

subplot_titles = [categorical_columns[0]] + ["m_depth"] + ["Ship distances"] + categorical_columns[1:]

fig = make_subplots(rows=len(categorical_columns), cols=cols, 
                    column_widths=[0.7, 0.15, 0.15],
                    shared_xaxes=True,
                    vertical_spacing=0.05,
                    horizontal_spacing = 0.03,
                    specs=specs,
                    subplot_titles=subplot_titles)

# Change subplot title size
fig.update_annotations(font_size=10)

# Add subplots
for i, col in enumerate(categorical_columns):
    fig.add_trace(go.Scatter(x=df["time"], y=df[col], line_shape='hv', name=col), row=i+1, col=1)
    fig.update_yaxes(type='category', categoryorder='array', categoryarray=np.sort(df[col].unique()), row=i+1, col=1)

fig.add_trace(go.Scatter(x=df["time"], y=df["m_depth"], name="m_depth"), row=1, col=2)
fig.add_trace(go.Scatter(x=[df["time"][0]], y=[df["m_depth"][0]], name="m_depth_current", mode="markers"), row=1, col=2)
fig.update_yaxes(autorange="reversed", row=1, col=2)

for col in distance_cols:
    fig.add_trace(go.Scatter(x=df["time"], y=df[col], name=col), row=1, col=3)
    fig.add_trace(go.Scatter(x=[df["time"][0]], y=[df[col][0]], name=f"{col}_current", mode="markers"), row=1, col=3)

fig.update_layout(height=len(categorical_columns)*100, width=1300)

# Create animation frames for vertical line
yref = [1] + list(range(cols + 1, len(categorical_columns)+cols))
frames = [go.Frame(data=[go.Scatter(visible=True)]*len(categorical_columns) +
                        [go.Scatter(visible=True), go.Scatter(x=[df["time"][i]], y=[df["m_depth"][i]])] +
                        sum([[go.Scatter(visible=True), go.Scatter(x=[df["time"][i]], y=[df[col][i]])] for col in distance_cols], []),
                   traces=list(range(len(fig.data))),
                   layout=dict(shapes=[dict(type="line", xref="x", yref=f"y{yref[n]}",
                                            x0=df["time"][i], y0=0, 
                                            x1=df["time"][i], y1=len(df[col].unique())-2, 
                                            line_width=3) for n,col in enumerate(categorical_columns)]), 
                   name=str(df["time"][i])) for i in df.index]
fig.update(frames=frames)

# Helper function for slider and buttons
def frame_args(duration):
    return {
            "frame": {"duration": duration},
            "mode": "immediate",
            "fromcurrent": True,
            "transition": {"duration": duration, "easing": "linear"},
        }

fr_duration=1000  # Frame duration in milliseconds

sliders = [
            {
                "pad": {"b": 10, "t": 50},
                "len": 0.9,
                "x": 0.1,
                "y": 0,
                "transition": {"duration": fr_duration},
                "steps": [
                    {
                        "args": [[f.name], frame_args(fr_duration)],
                        "label": f.name,
                        "method": "animate"
                    }
                    for k, f in enumerate(fig.frames)
                ],
            }
        ]


fig.update_layout(showlegend=False,
                  margin=dict(t=10, l=10, r=10),
                  sliders=sliders,
                  updatemenus = [
                        {
                        "buttons": [
                            {
                             "args": [None, frame_args(fr_duration)],
                             "label": "&#9654;", # play symbol
                             "method": "animate",
                            },
                            {
                             "args": [[None], frame_args(fr_duration)],
                             "label": "&#9724;", # pause symbol
                             "method": "animate",
                            }],
                        "direction": "left",
                        "pad": {"r": 10, "t": 70},
                        "type": "buttons",
                        "x": 0.1,
                        "y": 0,
                        }])

fig.show()

### Static vertical layout

In [10]:
# Base structure of plot
specs = len(categorical_columns)*[[{}]]
specs += 2*[[{"rowspan": 2}], [None]]
cols = 1

subplot_titles = categorical_columns + ["m_depth"] + ["Ship distances"]

fig = make_subplots(rows=len(categorical_columns)+4, cols=cols, 
                    shared_xaxes=True,
                    vertical_spacing=0.05,
                    horizontal_spacing = 0.03,
                    specs=specs,
                    subplot_titles=subplot_titles)

# Change subplot title size
fig.update_annotations(font_size=14)

# Add subplots
for i, col in enumerate(categorical_columns):
    fig.add_trace(go.Scatter(x=df["time"], y=df[col], line_shape='hv', name=col), row=i+1, col=1)
    fig.update_yaxes(type='category', categoryorder='array', categoryarray=np.sort(df[col].unique()), row=i+1, col=1)

fig.add_trace(go.Scatter(x=df["time"], y=df["m_depth"], name="m_depth"), row=i+2, col=1)
fig.update_yaxes(autorange="reversed", row=i+2, col=1)

for col in distance_cols:
    fig.add_trace(go.Scatter(x=df["time"], y=df[col], name=col), row=i+4, col=1)

fig.update_layout(height=(len(categorical_columns) + 4)*100, width=2500)

fig.update_layout(showlegend=False)

fig.show()

In [11]:
# fig.write_html("timeline_animation_2.html")

## Testing and Development

In [12]:
# Base structure of plot
specs = len(categorical_columns)*[[{}, None, None]]
specs[0] = [{}, {"rowspan": 5}, {"rowspan": 5}]
cols = 3

subplot_titles = [categorical_columns[0]] + ["m_depth"] + ["Ship distances"] + categorical_columns[1:]

fig = make_subplots(rows=len(categorical_columns), cols=cols, 
                    column_widths=[0.7, 0.15, 0.15],
                    shared_xaxes=True,
                    vertical_spacing=0.05,
                    horizontal_spacing = 0.03,
                    specs=specs,
                    subplot_titles=subplot_titles)

# Change subplot title size
fig.update_annotations(font_size=10)

# Add subplots
for i, col in enumerate(categorical_columns):
    fig.add_trace(go.Scatter(x=df["time"], y=df[col], line_shape='hv', name=col), row=i+1, col=1)
    fig.update_yaxes(type='category', categoryorder='array', categoryarray=np.sort(df[col].unique()), row=i+1, col=1)

fig.add_trace(go.Scatter(x=df["time"], y=df["m_depth"], name="m_depth"), row=1, col=2)
fig.update_yaxes(autorange="reversed", row=1, col=2)

for col in distance_cols:
    fig.add_trace(go.Scatter(x=df["time"], y=df[col], name=col), row=1, col=3)

fig.update_layout(height=len(categorical_columns)*100, width=1300)

# Create animation frames for vertical line
yref = [1] + list(range(cols + 1, len(categorical_columns)+cols))
frames = [go.Frame(layout=dict(shapes=[dict(type="line", xref="x", yref=f"y{yref[n]}",
                                            x0=df["time"][i], y0=0, 
                                            x1=df["time"][i], y1=len(df[col].unique())-2, 
                                            line_width=3) for n,col in enumerate(categorical_columns)] + 
                                      [dict(type="line", xref="x2", yref="y2",
                                            x0=df["time"][i], y0=df["m_depth"].max(), 
                                            x1=df["time"][i], y1=df["m_depth"].min(), 
                                            line_width=3)] +
                                      [dict(type="line", xref="x3", yref="y3",
                                            x0=df["time"][i], y0=df[distance_cols].min().min(), 
                                            x1=df["time"][i], y1=df[distance_cols].max().max(), 
                                            line_width=3)]
                                            ), 
                   name=str(df["time"][i])) for i in df.index]
fig.update(frames=frames)

# Helper function for slider and buttons
def frame_args(duration):
    return {
            "frame": {"duration": duration},
            "mode": "immediate",
            "fromcurrent": True,
            "transition": {"duration": duration, "easing": "linear"},
        }

fr_duration=1000  # Frame duration in milliseconds

sliders = [
            {
                "pad": {"b": 10, "t": 50},
                "len": 0.9,
                "x": 0.1,
                "y": 0,
                "transition": {"duration": fr_duration},
                "steps": [
                    {
                        "args": [[f.name], frame_args(fr_duration)],
                        "label": f.name,
                        "method": "animate"
                    }
                    for k, f in enumerate(fig.frames)
                ],
            }
        ]


fig.update_layout(showlegend=False,
                  margin=dict(t=10, l=10, r=10),
                  sliders=sliders,
                  updatemenus = [
                        {
                        "buttons": [
                            {
                             "args": [None, frame_args(fr_duration)],
                             "label": "&#9654;", # play symbol
                             "method": "animate",
                            },
                            {
                             "args": [[None], frame_args(fr_duration)],
                             "label": "&#9724;", # pause symbol
                             "method": "animate",
                            }],
                        "direction": "left",
                        "pad": {"r": 10, "t": 70},
                        "type": "buttons",
                        "x": 0.1,
                        "y": 0,
                        }])

fig.show()

In [ ]:
app = Dash(__name__)

app.layout = html.Div([
    dcc.Graph(id="graph"),
    html.P("Time"),
    dcc.RangeSlider(
        id='t-range-slider',
        # updatemode='drag',
        min=min(df.index), max=max(df.index), step=1,
        marks=None, # df['time'][idx] # {idx:'' for idx in range(len(df))}
        tooltip={"placement": "bottom", "always_visible": True},
        value=[min(df.index)]
    )
])

@app.callback(
    Output("graph", "figure"),
    [Input("t-range-slider", "value")])

def update_chart(slider_t):
    
    index = slider_t[0]
    
    # Base structure of plot
    specs = len(categorical_columns)*[[{}, None, None]]
    specs[0] = [{}, {"rowspan": 5}, {"rowspan": 5}]
    cols = 3

    subplot_titles = [categorical_columns[0]] + ["m_depth"] + ["Ship distances"] + categorical_columns[1:]

    fig = make_subplots(rows=len(categorical_columns), cols=cols, 
                        column_widths=[0.7, 0.15, 0.15],
                        shared_xaxes=True,
                        vertical_spacing=0.05,
                        horizontal_spacing = 0.03,
                        specs=specs,
                        subplot_titles=subplot_titles)

    # Change subplot title size
    fig.update_annotations(font_size=10)

    # Add subplots
    for i, col in enumerate(categorical_columns):
        fig.add_trace(go.Scatter(x=df["time"], y=df[col], line_shape='hv', name=col), row=i+1, col=1)
        fig.update_yaxes(type='category', categoryorder='array', categoryarray=np.sort(df[col].unique()), row=i+1, col=1)

    fig.add_trace(go.Scatter(x=df["time"], y=df["m_depth"], name="m_depth"), row=1, col=2)
    fig.add_trace(go.Scatter(x=[df.loc[index, "time"]], y=[df.loc[index, "m_depth"]], name="m_depth_current", mode="markers"), row=1, col=2)
    fig.update_yaxes(autorange="reversed", row=1, col=2)

    for col in distance_cols:
        fig.add_trace(go.Scatter(x=df["time"], y=df[col], name=col), row=1, col=3)
        fig.add_trace(go.Scatter(x=[df.loc[index, "time"]], y=[df.loc[index, col]], name=f"{col}_current", mode="markers"), row=1, col=3)
        
    fig.add_vline(x=df.loc[index, "time"], col=1, line_width=3)

    fig.update_layout(height=len(categorical_columns)*100, width=1250)

    fig.update_layout(showlegend=False,
                      margin=dict(t=10, l=10, r=10))
    

    return fig

app.run(debug=True,jupyter_height=700)